<a href="https://colab.research.google.com/github/dfili/clickbait_spoiling/blob/master/tar_projekt.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

### Installing

In [1]:
%pip install datasets

In [2]:
%pip install evaluate

In [3]:
# %pip install rouge_score

In [4]:
# %pip install bleu

In [5]:
%pip install accelerate -U

In [6]:
%pip install transformers[torch]

In [7]:
!nvidia-smi

Mon Jul  1 16:51:21 2024       
+---------------------------------------------------------------------------------------+
| NVIDIA-SMI 535.104.05             Driver Version: 535.104.05   CUDA Version: 12.2     |
|-----------------------------------------+----------------------+----------------------+
| GPU  Name                 Persistence-M | Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |         Memory-Usage | GPU-Util  Compute M. |
|                                         |                      |               MIG M. |
|=========================================+======================+======================|
|   0  Tesla V100-SXM2-16GB           Off | 00000000:00:04.0 Off |                    0 |
| N/A   36C    P0              24W / 300W |      0MiB / 16384MiB |      0%      Default |
|                                         |                      |                  N/A |
+-----------------------------------------+----------------------+--

## Imports

In [8]:
from transformers import pipeline, TrainingArguments, Trainer
import torch
import os

In [9]:
from datasets import load_dataset, Dataset
import datasets
import pandas as pd
import numpy as np
from torch.nn import CrossEntropyLoss
import torch.nn.functional as F
from torch.utils.data import Dataset, DataLoader
from transformers import AutoModelForQuestionAnswering, AutoTokenizer

In [10]:
import evaluate

In [11]:
import accelerate

In [12]:
from collections import defaultdict

In [13]:
from transformers import EvalPrediction

In [14]:
from collections import Counter

In [15]:
# from google.colab import drive
# drive.mount('/content/drive')

In [16]:
# import os
# import shutil

# directory_to_zip = '/results'  # Replace with the actual directory path
# output_filename = 'clickbait_res.zip'

# shutil.make_archive(output_filename.split('.')[0], 'zip', directory_to_zip)

In [17]:
# from google.colab import files
# files.download(output_filename)

### Question answering models

For QA models, input should be in form:
```json
QA_input = {
    'question': 'Why is model conversion important?',
    'context': 'The option to convert models between FARM and transformers gives freedom to the user and let people easily switch between frameworks.'
}
```

In [18]:
qa_model_names = ["deepset/roberta-base-squad2", "deepset/tinyroberta-squad2", "timpal0l/mdeberta-v3-base-squad2"]

qa_pipelines = []
qa_models = []
qa_tokenizers = []


for model_name in qa_model_names:
    qa_pipelines.append(pipeline('question-answering', model=model_name, tokenizer=model_name))
    qa_models.append(AutoModelForQuestionAnswering.from_pretrained(model_name))
    qa_tokenizers.append(AutoTokenizer.from_pretrained(model_name))


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


## Datasets

In [19]:
trainpath = "projekt_data/train.jsonl"
testpath = "projekt_data/test.jsonl"
validpath = "projekt_data/validation.jsonl"

In [20]:
train_dataset = load_dataset("json", data_files=trainpath, split="train")
# remove multi answer entries and preprocess
train_dataset = train_dataset.filter(lambda x: "multi" not in x["tags"] and x["targetTitle"] != "" and x["targetParagraphs"] != [])

In [21]:
valid_dataset = load_dataset("json", data_files=validpath, split="train")
valid_dataset = valid_dataset.filter(lambda x: "multi" not in x["tags"] and x["targetTitle"] != "" and x["targetParagraphs"] != [])

In [22]:
test_dataset = load_dataset("json", data_files=testpath, split="train")
test_dataset = test_dataset.filter(lambda x: "multi" not in x["tags"] and x["targetTitle"] != "" and x["targetParagraphs"] != [])

In [23]:
test_dataset["spoilerPositions"][0]

[[[4, 188], [4, 192]]]

In [24]:
type(test_dataset)

datasets.arrow_dataset.Dataset

## Data preprocessing

In [25]:
col_names = ["id", "question", "context", "answers"]

In [26]:
def cleanup_dataset_stringified(dataset):
  # remove multi answer entries and preprocess
  contexts = [" ".join(pars) for pars in dataset["targetParagraphs"]]
  answers = [answer[0] for answer in dataset["spoiler"]]
  new_dataset = dataset.select_columns(['uuid', 'targetTitle'])
  new_dataset = new_dataset.rename_columns({'uuid': 'id', 'targetTitle': 'question'})
  new_dataset = new_dataset.add_column("context", contexts)
  new_dataset = new_dataset.add_column("answers", answers)
  return new_dataset

In [27]:
clean_test_stringified = cleanup_dataset_stringified(test_dataset)
clean_valid_stringified = cleanup_dataset_stringified(valid_dataset)
clean_train_stringified = cleanup_dataset_stringified(train_dataset)

In [28]:
from datasets import Dataset
def cleanup_dataset_paragraphs(dataset):
  # remove multi answer entries and preprocess
  new_dataset = []
  for example in dataset:
    for paragraph in example["targetParagraphs"]:
        new_entry = {
            'id': example['uuid'],
            'question': example['targetTitle'],
            'answers': example['spoiler'][0],
            'context': paragraph
        }
        new_dataset.append(new_entry)
  new_dataset = Dataset.from_list(new_dataset)
  return new_dataset

In [29]:
clean_test_paragraphs = cleanup_dataset_paragraphs(test_dataset)
clean_valid_paragraphs = cleanup_dataset_paragraphs(valid_dataset)
clean_train_paragraphs = cleanup_dataset_paragraphs(train_dataset)
col_names = ["id", "question", "context", "answers"]

### Help functions

In [30]:
batch_size=5
metrics = evaluate.combine(["exact_match"])

# Precision = ratio of the number of shared words between the prediction and the truth to the total number of words in the prediction.
# Recall = ratio of the number of shared words between the prediction and the truth to the total number of words in the ground truth.
def compute_qa_metrics(tokenizer, input_ids):
    def compute_metrics(p):
        tp=0
        em=0
        total_pred=0
        total_ref=0

        start_preds, end_preds = p.predictions
        start_labels, end_labels = p.label_ids

        start_preds = np.argmax(start_preds, axis=-1)
        end_preds = np.argmax(end_preds, axis=-1)

        # Convert to lists of dictionaries as expected by the squad metric
        for i, (start_pred, end_pred, start_true, end_true) in enumerate(zip(start_preds, end_preds, start_labels, end_labels)):
            predicted_span = tokenizer.decode(input_ids[i][start_pred:end_pred+1])
            true_span = tokenizer.decode(input_ids[i][start_true:end_true+1])

            em += start_pred == start_true and end_pred == end_true

            tp += sum([len(set(p.split())&set(r.split())) for p, r in zip(predicted_span, true_span)])
            total_pred += sum([len(p.split()) for p in predicted_span])
            total_ref += sum([len(r.split()) for r in true_span])
            metrics.add(predictions=predicted_span, references=true_span)

        precision = tp/total_pred
        recall = tp/total_ref
        f1 = 2 * (precision * recall) / (precision + recall)
        em = em/len(start_preds)

        print(f"F1: {f1:.4f}")
        print(f"Exact match: {em}")
        print(f"Precision: {precision:.4f}")
        print(f"Recall: {recall:.4f}")
        #metrics.compute(ignore_case=True)

        return {"Precision":precision, "Recall": recall,"F1": f1, "Exact match": em} #, "Metrics": metrics}
    return compute_metrics


In [31]:
def run_eval(model, tokenizer, dataset, training_args):
    # Initialize the Trainer
    trainer = Trainer(
        model=model,
        args=training_args,
        eval_dataset=dataset,
        tokenizer=tokenizer,
        compute_metrics=compute_qa_metrics(tokenizer, dataset["input_ids"]),
    )

    # Evaluate the model
    eval_results = trainer.evaluate()
    print(eval_results)
    return eval_results

## Cutoff

In [32]:
def preprocess_dataset_cutoff(dataset, tokenizer):
    start_positions = []
    end_positions = []

    contexts = dataset["context"]
    answers = dataset["answers"]

    max_length = tokenizer.model_max_length
    if max_length is None or max_length > 2048:
        max_length = 2048

    inputs = tokenizer(
          dataset["question"],
          contexts,
          max_length=max_length,
          truncation="only_second",
          padding="max_length",
          return_offsets_mapping=True,
    )

    offset_mapping = inputs.pop("offset_mapping")

    for i, offsets in enumerate(offset_mapping):
          answer = answers[i]
          context = contexts[i]
          start_char = context.find(answer)
          end_char = start_char + len(answer)

          start_position = None
          end_position = None

          for j, (start, end) in enumerate(offsets):
              if start <= start_char < end:
                  start_position = j
              if start < end_char <= end:
                  end_position = j

          # Ensure we have valid positions
          if start_position is None or end_position is None:
              start_positions.append(0)
              end_positions.append(0)
          else:
              start_positions.append(start_position)
              end_positions.append(end_position)

    inputs.update({
        "start_positions": start_positions,
        "end_positions": end_positions
    })
    return inputs

Model1

In [33]:
training_args = TrainingArguments(
    output_dir="./results/pretrained/cutoff/qa_0",
    per_device_eval_batch_size=8,
)
model = qa_models[0]
tokenizer = qa_tokenizers[0]
preprocessed_test_cutoff0 = clean_test_stringified.map(preprocess_dataset_cutoff, batched=True, remove_columns=col_names, fn_kwargs={"tokenizer":qa_tokenizers[0]})
preprocessed_train_cutoff0 = clean_train_stringified.map(preprocess_dataset_cutoff, batched=True, remove_columns=col_names, fn_kwargs={"tokenizer":qa_tokenizers[0]})
preprocessed_valid_cutoff0 = clean_valid_stringified.map(preprocess_dataset_cutoff, batched=True, remove_columns=col_names, fn_kwargs={"tokenizer":qa_tokenizers[0]})

dataset = preprocessed_test_cutoff0
res = run_eval(model, tokenizer, dataset, training_args)

Map:   0%|          | 0/825 [00:00<?, ? examples/s]

Map:   0%|          | 0/2640 [00:00<?, ? examples/s]

Map:   0%|          | 0/656 [00:00<?, ? examples/s]

F1: 0.0504
Exact match: 0.12121212121212122
Precision: 0.0632
Recall: 0.0419
{'eval_loss': 4.487522125244141, 'eval_Precision': 0.0632462203822127, 'eval_Recall': 0.04193833031030933, 'eval_F1': 0.05043403929197801, 'eval_Exact match': 0.12121212121212122, 'eval_runtime': 11.1772, 'eval_samples_per_second': 73.811, 'eval_steps_per_second': 9.305}


In [34]:
training_args = TrainingArguments(
    output_dir='./results/fine-tuned/cutoff/qa_0',
    eval_strategy="epoch",
    save_strategy="epoch",
    learning_rate=2e-5,
    per_device_train_batch_size=8,
    per_device_eval_batch_size=8,
    num_train_epochs=3,
    weight_decay=0.01,
    logging_dir='./logs',
    logging_steps=10,
    logging_first_step=True,
    log_level='info'
)

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=preprocessed_train_cutoff0,
    eval_dataset=preprocessed_valid_cutoff0,
    compute_metrics=compute_qa_metrics(tokenizer, preprocessed_valid_cutoff0["input_ids"])
)

trainer.train()

***** Running training *****
  Num examples = 2,640
  Num Epochs = 3
  Instantaneous batch size per device = 8
  Total train batch size (w. parallel, distributed & accumulation) = 8
  Gradient Accumulation steps = 1
  Total optimization steps = 990
  Number of trainable parameters = 124,056,578


***** Running Evaluation *****
  Num examples = 656
  Batch size = 8


F1: 0.1299
Exact match: 0.25609756097560976
Precision: 0.1074
Recall: 0.1643


Saving model checkpoint to ./results/fine-tuned/cutoff/qa_0/checkpoint-330
Configuration saved in ./results/fine-tuned/cutoff/qa_0/checkpoint-330/config.json
Model weights saved in ./results/fine-tuned/cutoff/qa_0/checkpoint-330/model.safetensors
***** Running Evaluation *****
  Num examples = 656
  Batch size = 8


F1: 0.1206
Exact match: 0.25
Precision: 0.0943
Recall: 0.1673


Saving model checkpoint to ./results/fine-tuned/cutoff/qa_0/checkpoint-660
Configuration saved in ./results/fine-tuned/cutoff/qa_0/checkpoint-660/config.json
Model weights saved in ./results/fine-tuned/cutoff/qa_0/checkpoint-660/model.safetensors
***** Running Evaluation *****
  Num examples = 656
  Batch size = 8


F1: 0.1220
Exact match: 0.24695121951219512
Precision: 0.1016
Recall: 0.1527


Saving model checkpoint to ./results/fine-tuned/cutoff/qa_0/checkpoint-990
Configuration saved in ./results/fine-tuned/cutoff/qa_0/checkpoint-990/config.json
Model weights saved in ./results/fine-tuned/cutoff/qa_0/checkpoint-990/model.safetensors


Training completed. Do not forget to share your model on huggingface.co/models =)




TrainOutput(global_step=990, training_loss=2.154750773882625, metrics={'train_runtime': 350.4017, 'train_samples_per_second': 22.603, 'train_steps_per_second': 2.825, 'total_flos': 2069470313349120.0, 'train_loss': 2.154750773882625, 'epoch': 3.0})

In [35]:
save_dir_cutoff0 = './results/fine-tuned/cutoff/qa_0/model'
trainer.save_model(save_dir_cutoff0)
tokenizer.save_pretrained(save_dir_cutoff0)
print(tokenizer)

Saving model checkpoint to ./results/fine-tuned/cutoff/qa_0/model
Configuration saved in ./results/fine-tuned/cutoff/qa_0/model/config.json
Model weights saved in ./results/fine-tuned/cutoff/qa_0/model/model.safetensors
tokenizer config file saved in ./results/fine-tuned/cutoff/qa_0/model/tokenizer_config.json
Special tokens file saved in ./results/fine-tuned/cutoff/qa_0/model/special_tokens_map.json


RobertaTokenizerFast(name_or_path='deepset/roberta-base-squad2', vocab_size=50265, model_max_length=512, is_fast=True, padding_side='right', truncation_side='right', special_tokens={'bos_token': '<s>', 'eos_token': '</s>', 'unk_token': '<unk>', 'sep_token': '</s>', 'pad_token': '<pad>', 'cls_token': '<s>', 'mask_token': '<mask>'}, clean_up_tokenization_spaces=True),  added_tokens_decoder={
	0: AddedToken("<s>", rstrip=False, lstrip=False, single_word=False, normalized=True, special=True),
	1: AddedToken("<pad>", rstrip=False, lstrip=False, single_word=False, normalized=True, special=True),
	2: AddedToken("</s>", rstrip=False, lstrip=False, single_word=False, normalized=True, special=True),
	3: AddedToken("<unk>", rstrip=False, lstrip=False, single_word=False, normalized=True, special=True),
	50264: AddedToken("<mask>", rstrip=False, lstrip=True, single_word=False, normalized=True, special=True),
}


In [36]:
from transformers import RobertaForQuestionAnswering, AutoTokenizer

# Load the fine-tuned model and tokenizer
model = trainer.model

training_args = TrainingArguments(
    output_dir='./results/fine-tuned/cutoff/qa_0/eval',
    per_device_eval_batch_size=8,
)

trainer = Trainer(
    model=model,
    args=training_args,
    eval_dataset=preprocessed_test_cutoff0,
    compute_metrics=compute_qa_metrics(tokenizer, preprocessed_test_cutoff0["input_ids"]) # ako trebam predati input_ids, a oni su ovisni o datasetu, koje predajem?
)
trainer.evaluate()

PyTorch: setting up devices
The default value for the training argument `--report_to` will change in v5 (from all installed integrations to none). In v5, you will need to use `--report_to all` to get the same behavior as now. You should start updating your code and make this info disappear :-).
***** Running Evaluation *****
  Num examples = 825
  Batch size = 8


F1: 0.1664
Exact match: 0.24606060606060606
Precision: 0.1495
Recall: 0.1876


{'eval_loss': 3.077378034591675,
 'eval_Precision': 0.14951353885828156,
 'eval_Recall': 0.18758272464336487,
 'eval_F1': 0.1663985040876674,
 'eval_Exact match': 0.24606060606060606,
 'eval_runtime': 10.3595,
 'eval_samples_per_second': 79.637,
 'eval_steps_per_second': 10.039}

Model2

In [37]:
training_args = TrainingArguments(
    output_dir="./results/pretrained/cutoff/qa_1",
    per_device_eval_batch_size=8,
)
model = qa_models[1]
tokenizer = qa_tokenizers[1]
preprocessed_test_cutoff1 = clean_test_stringified.map(preprocess_dataset_cutoff, batched=True, remove_columns=col_names, fn_kwargs={"tokenizer":qa_tokenizers[1]})
preprocessed_train_cutoff1 = clean_train_stringified.map(preprocess_dataset_cutoff, batched=True, remove_columns=col_names, fn_kwargs={"tokenizer":qa_tokenizers[1]})
preprocessed_valid_cutoff1 = clean_valid_stringified.map(preprocess_dataset_cutoff, batched=True, remove_columns=col_names, fn_kwargs={"tokenizer":qa_tokenizers[1]})

dataset = preprocessed_test_cutoff1
res = run_eval(model, tokenizer, dataset, training_args)

PyTorch: setting up devices
The default value for the training argument `--report_to` will change in v5 (from all installed integrations to none). In v5, you will need to use `--report_to all` to get the same behavior as now. You should start updating your code and make this info disappear :-).


Map:   0%|          | 0/825 [00:00<?, ? examples/s]

Map:   0%|          | 0/2640 [00:00<?, ? examples/s]

Map:   0%|          | 0/656 [00:00<?, ? examples/s]

***** Running Evaluation *****
  Num examples = 825
  Batch size = 8


F1: 0.0250
Exact match: 0.0993939393939394
Precision: 0.0968
Recall: 0.0144
{'eval_loss': 7.862128257751465, 'eval_Precision': 0.09684349694265411, 'eval_Recall': 0.01436344918868572, 'eval_F1': 0.02501654250891161, 'eval_Exact match': 0.0993939393939394, 'eval_runtime': 4.8949, 'eval_samples_per_second': 168.544, 'eval_steps_per_second': 21.247}


In [38]:
training_args = TrainingArguments(
    output_dir='./results/fine-tuned/cutoff/qa_1',
    eval_strategy="epoch",
    save_strategy="epoch",
    learning_rate=2e-5,
    per_device_train_batch_size=8,
    per_device_eval_batch_size=8,
    num_train_epochs=3,
    weight_decay=0.01,
    logging_dir='./logs',
    logging_steps=10,
    logging_first_step=True,
    log_level='info'
)

qa_trainer2 = Trainer(
    model=model,
    args=training_args,
    train_dataset=preprocessed_train_cutoff1,
    eval_dataset=preprocessed_valid_cutoff1,
    compute_metrics=compute_qa_metrics(tokenizer, preprocessed_valid_cutoff1["input_ids"])
)

qa_trainer2.train()

PyTorch: setting up devices
The default value for the training argument `--report_to` will change in v5 (from all installed integrations to none). In v5, you will need to use `--report_to all` to get the same behavior as now. You should start updating your code and make this info disappear :-).
***** Running training *****
  Num examples = 2,640
  Num Epochs = 3
  Instantaneous batch size per device = 8
  Total train batch size (w. parallel, distributed & accumulation) = 8
  Gradient Accumulation steps = 1
  Total optimization steps = 990
  Number of trainable parameters = 81,529,346


***** Running Evaluation *****
  Num examples = 656
  Batch size = 8


F1: 0.0958
Exact match: 0.19969512195121952
Precision: 0.0796
Recall: 0.1201


Saving model checkpoint to ./results/fine-tuned/cutoff/qa_1/checkpoint-330
Configuration saved in ./results/fine-tuned/cutoff/qa_1/checkpoint-330/config.json
Model weights saved in ./results/fine-tuned/cutoff/qa_1/checkpoint-330/model.safetensors
***** Running Evaluation *****
  Num examples = 656
  Batch size = 8


F1: 0.1030
Exact match: 0.19817073170731708
Precision: 0.0833
Recall: 0.1350


Saving model checkpoint to ./results/fine-tuned/cutoff/qa_1/checkpoint-660
Configuration saved in ./results/fine-tuned/cutoff/qa_1/checkpoint-660/config.json
Model weights saved in ./results/fine-tuned/cutoff/qa_1/checkpoint-660/model.safetensors
***** Running Evaluation *****
  Num examples = 656
  Batch size = 8


F1: 0.1148
Exact match: 0.2027439024390244
Precision: 0.0980
Recall: 0.1385


Saving model checkpoint to ./results/fine-tuned/cutoff/qa_1/checkpoint-990
Configuration saved in ./results/fine-tuned/cutoff/qa_1/checkpoint-990/config.json
Model weights saved in ./results/fine-tuned/cutoff/qa_1/checkpoint-990/model.safetensors


Training completed. Do not forget to share your model on huggingface.co/models =)




TrainOutput(global_step=990, training_loss=2.5745853347007674, metrics={'train_runtime': 196.4696, 'train_samples_per_second': 40.312, 'train_steps_per_second': 5.039, 'total_flos': 1034772552253440.0, 'train_loss': 2.5745853347007674, 'epoch': 3.0})

In [39]:
save_dir_cutoff1 = './results/fine-tuned/cutoff/qa_1/model'
trainer.save_model(save_dir_cutoff1)
tokenizer.save_pretrained(save_dir_cutoff1)
print(tokenizer)

Saving model checkpoint to ./results/fine-tuned/cutoff/qa_1/model
Configuration saved in ./results/fine-tuned/cutoff/qa_1/model/config.json
Model weights saved in ./results/fine-tuned/cutoff/qa_1/model/model.safetensors
tokenizer config file saved in ./results/fine-tuned/cutoff/qa_1/model/tokenizer_config.json
Special tokens file saved in ./results/fine-tuned/cutoff/qa_1/model/special_tokens_map.json


RobertaTokenizerFast(name_or_path='deepset/tinyroberta-squad2', vocab_size=50265, model_max_length=512, is_fast=True, padding_side='right', truncation_side='right', special_tokens={'bos_token': '<s>', 'eos_token': '</s>', 'unk_token': '<unk>', 'sep_token': '</s>', 'pad_token': '<pad>', 'cls_token': '<s>', 'mask_token': '<mask>'}, clean_up_tokenization_spaces=True),  added_tokens_decoder={
	0: AddedToken("<s>", rstrip=False, lstrip=False, single_word=False, normalized=False, special=True),
	1: AddedToken("<pad>", rstrip=False, lstrip=False, single_word=False, normalized=False, special=True),
	2: AddedToken("</s>", rstrip=False, lstrip=False, single_word=False, normalized=False, special=True),
	3: AddedToken("<unk>", rstrip=False, lstrip=False, single_word=False, normalized=False, special=True),
	50264: AddedToken("<mask>", rstrip=False, lstrip=True, single_word=False, normalized=False, special=True),
}


In [40]:
# Load the fine-tuned model and tokenizer
model = trainer.model

training_args = TrainingArguments(
    output_dir='results/fine-tuned/cutoff/qa_1/eval',
    per_device_eval_batch_size=8,
)

trainer = Trainer(
    model=model,
    args=training_args,
    eval_dataset=preprocessed_test_cutoff1,
    compute_metrics=compute_qa_metrics(tokenizer, preprocessed_test_cutoff1["input_ids"]) # ako trebam predati input_ids, a oni su ovisni o datasetu, koje predajem?
)
trainer.evaluate()

PyTorch: setting up devices
The default value for the training argument `--report_to` will change in v5 (from all installed integrations to none). In v5, you will need to use `--report_to all` to get the same behavior as now. You should start updating your code and make this info disappear :-).
***** Running Evaluation *****
  Num examples = 825
  Batch size = 8


F1: 0.1664
Exact match: 0.24606060606060606
Precision: 0.1495
Recall: 0.1876


{'eval_loss': 3.077378034591675,
 'eval_Precision': 0.14951353885828156,
 'eval_Recall': 0.18758272464336487,
 'eval_F1': 0.1663985040876674,
 'eval_Exact match': 0.24606060606060606,
 'eval_runtime': 9.3644,
 'eval_samples_per_second': 88.1,
 'eval_steps_per_second': 11.106}

Model3

In [33]:
preprocessed_test_cutoff2 = clean_test_stringified.map(preprocess_dataset_cutoff, batched=True, remove_columns=col_names, fn_kwargs={"tokenizer":qa_tokenizers[2]})
preprocessed_train_cutoff2 = clean_train_stringified.map(preprocess_dataset_cutoff, batched=True, remove_columns=col_names, fn_kwargs={"tokenizer":qa_tokenizers[2]})
preprocessed_valid_cutoff2 = clean_valid_stringified.map(preprocess_dataset_cutoff, batched=True, remove_columns=col_names, fn_kwargs={"tokenizer":qa_tokenizers[2]})


Map:   0%|          | 0/656 [00:00<?, ? examples/s]

In [33]:
training_args = TrainingArguments(
    output_dir="./results/pretrained/cutoff/qa_2",
    per_device_eval_batch_size=4,
)
model = qa_models[2]
tokenizer = qa_tokenizers[2]
dataset = preprocessed_test_cutoff2
res = run_eval(model, tokenizer, dataset, training_args)

Map:   0%|          | 0/2640 [00:00<?, ? examples/s]

F1: 0.0336
Exact match: 0.06666666666666667
Precision: 0.0241
Recall: 0.0551
{'eval_loss': 5.1140241622924805, 'eval_Precision': 0.02414251781472684, 'eval_Recall': 0.05511811023622047, 'eval_F1': 0.03357757794794881, 'eval_Exact match': 0.06666666666666667, 'eval_runtime': 115.4622, 'eval_samples_per_second': 7.145, 'eval_steps_per_second': 1.793}


In [36]:
model = qa_models[2]
tokenizer = qa_tokenizers[2]
training_args = TrainingArguments(
    output_dir='./results/fine-tuned/cutoff/qa_2',
    eval_strategy="epoch",
    save_strategy="epoch",
    learning_rate=2e-5,
    per_device_train_batch_size=1,
    per_device_eval_batch_size=1,
    num_train_epochs=3,
    weight_decay=0.01,
    logging_dir='./logs',
    logging_steps=10,
    logging_first_step=True,
    log_level='info'
)

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=preprocessed_train_cutoff2,
    eval_dataset=preprocessed_valid_cutoff2,
    compute_metrics=compute_qa_metrics(tokenizer, preprocessed_valid_cutoff2["input_ids"])
)

trainer.train()

PyTorch: setting up devices
The default value for the training argument `--report_to` will change in v5 (from all installed integrations to none). In v5, you will need to use `--report_to all` to get the same behavior as now. You should start updating your code and make this info disappear :-).
***** Running training *****
  Num examples = 2,640
  Num Epochs = 3
  Instantaneous batch size per device = 1
  Total train batch size (w. parallel, distributed & accumulation) = 1
  Gradient Accumulation steps = 1
  Total optimization steps = 7,920
  Number of trainable parameters = 278,220,290


***** Running Evaluation *****
  Num examples = 656
  Batch size = 1


F1: 0.1105
Exact match: 0.21798780487804878
Precision: 0.0812
Recall: 0.1725


Saving model checkpoint to ./results/fine-tuned/cutoff/qa_2/checkpoint-2640
Configuration saved in ./results/fine-tuned/cutoff/qa_2/checkpoint-2640/config.json
Model weights saved in ./results/fine-tuned/cutoff/qa_2/checkpoint-2640/model.safetensors
***** Running Evaluation *****
  Num examples = 656
  Batch size = 1


F1: 0.1290
Exact match: 0.22408536585365854
Precision: 0.1001
Recall: 0.1816


Saving model checkpoint to ./results/fine-tuned/cutoff/qa_2/checkpoint-5280
Configuration saved in ./results/fine-tuned/cutoff/qa_2/checkpoint-5280/config.json
Model weights saved in ./results/fine-tuned/cutoff/qa_2/checkpoint-5280/model.safetensors
***** Running Evaluation *****
  Num examples = 656
  Batch size = 1


F1: 0.1348
Exact match: 0.22865853658536586
Precision: 0.1061
Recall: 0.1847


Saving model checkpoint to ./results/fine-tuned/cutoff/qa_2/checkpoint-7920
Configuration saved in ./results/fine-tuned/cutoff/qa_2/checkpoint-7920/config.json
Model weights saved in ./results/fine-tuned/cutoff/qa_2/checkpoint-7920/model.safetensors


Training completed. Do not forget to share your model on huggingface.co/models =)




TrainOutput(global_step=7920, training_loss=2.41241811372415, metrics={'train_runtime': 3709.3989, 'train_samples_per_second': 2.135, 'train_steps_per_second': 2.135, 'total_flos': 8278030738391040.0, 'train_loss': 2.41241811372415, 'epoch': 3.0})

In [37]:
save_dir_cutoff3 = './results/fine-tuned/cutoff/qa_1/model'
trainer.save_model(save_dir_cutoff3)
tokenizer.save_pretrained(save_dir_cutoff3)


Saving model checkpoint to ./results/fine-tuned/cutoff/qa_1/model
Configuration saved in ./results/fine-tuned/cutoff/qa_1/model/config.json
Model weights saved in ./results/fine-tuned/cutoff/qa_1/model/model.safetensors
tokenizer config file saved in ./results/fine-tuned/cutoff/qa_1/model/tokenizer_config.json
Special tokens file saved in ./results/fine-tuned/cutoff/qa_1/model/special_tokens_map.json


('./results/fine-tuned/cutoff/qa_1/model/tokenizer_config.json',
 './results/fine-tuned/cutoff/qa_1/model/special_tokens_map.json',
 './results/fine-tuned/cutoff/qa_1/model/tokenizer.json')

In [40]:
# Load the fine-tuned model and tokenizer
model = trainer.model

training_args = TrainingArguments(
    output_dir='results/fine-tuned/cutoff/qa_2/eval',
    per_device_eval_batch_size=2,
)

trainer = Trainer(
    model=model,
    args=training_args,
    eval_dataset=preprocessed_test_cutoff2,
    compute_metrics=compute_qa_metrics(tokenizer, preprocessed_test_cutoff2["input_ids"]) # ako trebam predati input_ids, a oni su ovisni o datasetu, koje predajem?
)
trainer.evaluate()

PyTorch: setting up devices
The default value for the training argument `--report_to` will change in v5 (from all installed integrations to none). In v5, you will need to use `--report_to all` to get the same behavior as now. You should start updating your code and make this info disappear :-).
***** Running Evaluation *****
  Num examples = 825
  Batch size = 2


F1: 0.1482
Exact match: 0.21212121212121213
Precision: 0.1182
Recall: 0.1986


{'eval_loss': 4.3789262771606445,
 'eval_Precision': 0.11819531401277997,
 'eval_Recall': 0.19860740547927377,
 'eval_F1': 0.14819610572487577,
 'eval_Exact match': 0.21212121212121213,
 'eval_runtime': 117.5944,
 'eval_samples_per_second': 7.016,
 'eval_steps_per_second': 3.512}

## Remove long

In [31]:
def preprocess_dataset_remove_long(dataset, tokenizer):
    contexts = []
    answers = []
    questions = []

    max_length = tokenizer.model_max_length
    if max_length is None or max_length > 2048:
        max_length = 2048

    for c, a, q in zip(dataset["context"], dataset["answers"], dataset["question"]):
        if len(c+a) < max_length:
            contexts.append(c)
            answers.append(a)
            questions.append(q)

    start_positions = []
    end_positions = []

    inputs = tokenizer(
          questions,
          contexts,
          max_length=max_length,
          truncation="only_second",
          padding="max_length",
          return_offsets_mapping=True,
    )

    offset_mapping = inputs.pop("offset_mapping")

    for i, offsets in enumerate(offset_mapping):
          answer = answers[i]
          context = contexts[i]
          start_char = context.find(answer)
          end_char = start_char + len(answer)

          start_position = None
          end_position = None

          for j, (start, end) in enumerate(offsets):
              if start <= start_char < end:
                  start_position = j
              if start < end_char <= end:
                  end_position = j

          # Ensure we have valid positions
          if start_position is None or end_position is None:
              start_positions.append(0)
              end_positions.append(0)
          else:
              start_positions.append(start_position)
              end_positions.append(end_position)

    inputs.update({
        "start_positions": start_positions,
        "end_positions": end_positions
    })
    return inputs

Model1

In [45]:
preprocessed_test_rl0 = clean_test_stringified.map(preprocess_dataset_remove_long, batched=True, remove_columns=col_names, fn_kwargs={"tokenizer":qa_tokenizers[0]})
preprocessed_train_rl0 = clean_train_stringified.map(preprocess_dataset_remove_long, batched=True, remove_columns=col_names, fn_kwargs={"tokenizer":qa_tokenizers[0]})
preprocessed_valid_rl0 = clean_valid_stringified.map(preprocess_dataset_remove_long, batched=True, remove_columns=col_names, fn_kwargs={"tokenizer":qa_tokenizers[0]})


Map:   0%|          | 0/825 [00:00<?, ? examples/s]

Map:   0%|          | 0/2640 [00:00<?, ? examples/s]

Map:   0%|          | 0/656 [00:00<?, ? examples/s]

In [46]:
training_args = TrainingArguments(
    output_dir="./results/pretrained/remove_long/qa_0",
    per_device_eval_batch_size=8,
)
model = qa_models[0]
tokenizer = qa_tokenizers[0]

dataset = preprocessed_test_rl0
res = run_eval(model, tokenizer, dataset, training_args)

PyTorch: setting up devices
The default value for the training argument `--report_to` will change in v5 (from all installed integrations to none). In v5, you will need to use `--report_to all` to get the same behavior as now. You should start updating your code and make this info disappear :-).
***** Running Evaluation *****
  Num examples = 24
  Batch size = 8


F1: 0.0858
Exact match: 0.20833333333333334
Precision: 0.1930
Recall: 0.0552
{'eval_loss': 3.409796953201294, 'eval_Precision': 0.19298245614035087, 'eval_Recall': 0.05518394648829431, 'eval_F1': 0.0858257477243173, 'eval_Exact match': 0.20833333333333334, 'eval_runtime': 0.3246, 'eval_samples_per_second': 73.927, 'eval_steps_per_second': 9.241}


In [47]:
training_args = TrainingArguments(
    output_dir='./results/fine-tuned/remove_long/qa_0',
    eval_strategy="epoch",
    save_strategy="epoch",
    learning_rate=2e-5,
    per_device_train_batch_size=8,
    per_device_eval_batch_size=8,
    num_train_epochs=3,
    weight_decay=0.01,
    logging_dir='./logs',
    logging_steps=10,
    logging_first_step=True,
    log_level='info'
)

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=preprocessed_train_rl0,
    eval_dataset=preprocessed_valid_rl0 ,
    compute_metrics=compute_qa_metrics(tokenizer, preprocessed_valid_rl0["input_ids"])
)

trainer.train()

PyTorch: setting up devices
The default value for the training argument `--report_to` will change in v5 (from all installed integrations to none). In v5, you will need to use `--report_to all` to get the same behavior as now. You should start updating your code and make this info disappear :-).
***** Running training *****
  Num examples = 82
  Num Epochs = 3
  Instantaneous batch size per device = 8
  Total train batch size (w. parallel, distributed & accumulation) = 8
  Gradient Accumulation steps = 1
  Total optimization steps = 33
  Number of trainable parameters = 124,056,578


***** Running Evaluation *****
  Num examples = 14
  Batch size = 8


F1: 0.0588
Exact match: 0.14285714285714285
Precision: 0.0560
Recall: 0.0620


Saving model checkpoint to ./results/fine-tuned/remove_long/qa_0/checkpoint-11
Configuration saved in ./results/fine-tuned/remove_long/qa_0/checkpoint-11/config.json
Model weights saved in ./results/fine-tuned/remove_long/qa_0/checkpoint-11/model.safetensors
***** Running Evaluation *****
  Num examples = 14
  Batch size = 8


F1: 0.0630
Exact match: 0.14285714285714285
Precision: 0.0665
Recall: 0.0599


Saving model checkpoint to ./results/fine-tuned/remove_long/qa_0/checkpoint-22
Configuration saved in ./results/fine-tuned/remove_long/qa_0/checkpoint-22/config.json
Model weights saved in ./results/fine-tuned/remove_long/qa_0/checkpoint-22/model.safetensors
***** Running Evaluation *****
  Num examples = 14
  Batch size = 8


F1: 0.0588
Exact match: 0.14285714285714285
Precision: 0.0621
Recall: 0.0558


Saving model checkpoint to ./results/fine-tuned/remove_long/qa_0/checkpoint-33
Configuration saved in ./results/fine-tuned/remove_long/qa_0/checkpoint-33/config.json
Model weights saved in ./results/fine-tuned/remove_long/qa_0/checkpoint-33/model.safetensors


Training completed. Do not forget to share your model on huggingface.co/models =)




TrainOutput(global_step=33, training_loss=1.6798855246919575, metrics={'train_runtime': 65.3424, 'train_samples_per_second': 3.765, 'train_steps_per_second': 0.505, 'total_flos': 64279002157056.0, 'train_loss': 1.6798855246919575, 'epoch': 3.0})

In [48]:
save_dir_rl1 = './results/fine-tuned/remove_long/qa_0/model'
trainer.save_model(save_dir_rl1)
tokenizer.save_pretrained(save_dir_rl1)


Saving model checkpoint to ./results/fine-tuned/remove_long/qa_0/model
Configuration saved in ./results/fine-tuned/remove_long/qa_0/model/config.json
Model weights saved in ./results/fine-tuned/remove_long/qa_0/model/model.safetensors
tokenizer config file saved in ./results/fine-tuned/remove_long/qa_0/model/tokenizer_config.json
Special tokens file saved in ./results/fine-tuned/remove_long/qa_0/model/special_tokens_map.json


('./results/fine-tuned/remove_long/qa_0/model/tokenizer_config.json',
 './results/fine-tuned/remove_long/qa_0/model/special_tokens_map.json',
 './results/fine-tuned/remove_long/qa_0/model/vocab.json',
 './results/fine-tuned/remove_long/qa_0/model/merges.txt',
 './results/fine-tuned/remove_long/qa_0/model/added_tokens.json',
 './results/fine-tuned/remove_long/qa_0/model/tokenizer.json')

In [49]:
# Load the fine-tuned model and tokenizer
model = trainer.model
training_args = TrainingArguments(
    output_dir='results/fine-tuned/remove_long/qa_0/eval',
    per_device_eval_batch_size=8,
)

trainer = Trainer(
    model=model,
    args=training_args,
    eval_dataset=preprocessed_test_rl0,
    compute_metrics=compute_qa_metrics(tokenizer, preprocessed_test_rl0["input_ids"]) # ako trebam predati input_ids, a oni su ovisni o datasetu, koje predajem?
)
trainer.evaluate()

PyTorch: setting up devices
The default value for the training argument `--report_to` will change in v5 (from all installed integrations to none). In v5, you will need to use `--report_to all` to get the same behavior as now. You should start updating your code and make this info disappear :-).
***** Running Evaluation *****
  Num examples = 24
  Batch size = 8


F1: 0.3791
Exact match: 0.3333333333333333
Precision: 0.3949
Recall: 0.3645


{'eval_loss': 2.090770959854126,
 'eval_Precision': 0.39492753623188404,
 'eval_Recall': 0.36454849498327757,
 'eval_F1': 0.37913043478260866,
 'eval_Exact match': 0.3333333333333333,
 'eval_runtime': 0.284,
 'eval_samples_per_second': 84.521,
 'eval_steps_per_second': 10.565}

Model2

In [50]:
training_args = TrainingArguments(
    output_dir="./results/pretrained/remove_long/qa_1",
    per_device_eval_batch_size=8,
)
model = qa_models[1]
tokenizer = qa_tokenizers[1]
preprocessed_test_rl1 = clean_test_stringified.map(preprocess_dataset_remove_long, batched=True, remove_columns=col_names, fn_kwargs={"tokenizer":qa_tokenizers[1]})
preprocessed_train_rl1 = clean_train_stringified.map(preprocess_dataset_remove_long, batched=True, remove_columns=col_names, fn_kwargs={"tokenizer":qa_tokenizers[1]})
preprocessed_valid_rl1 = clean_valid_stringified.map(preprocess_dataset_remove_long, batched=True, remove_columns=col_names, fn_kwargs={"tokenizer":qa_tokenizers[1]})

dataset = preprocessed_test_rl1
res = run_eval(model, tokenizer, dataset, training_args)

PyTorch: setting up devices
The default value for the training argument `--report_to` will change in v5 (from all installed integrations to none). In v5, you will need to use `--report_to all` to get the same behavior as now. You should start updating your code and make this info disappear :-).


Map:   0%|          | 0/825 [00:00<?, ? examples/s]

Map:   0%|          | 0/2640 [00:00<?, ? examples/s]

Map:   0%|          | 0/656 [00:00<?, ? examples/s]

***** Running Evaluation *****
  Num examples = 24
  Batch size = 8


F1: 0.0413
Exact match: 0.16666666666666666
Precision: 0.1163
Recall: 0.0251
{'eval_loss': 5.935808181762695, 'eval_Precision': 0.11627906976744186, 'eval_Recall': 0.02508361204013378, 'eval_F1': 0.04126547455295736, 'eval_Exact match': 0.16666666666666666, 'eval_runtime': 0.1547, 'eval_samples_per_second': 155.16, 'eval_steps_per_second': 19.395}


In [51]:
training_args = TrainingArguments(
    output_dir='./results/fine-tuned/remove_long/qa_1',
    eval_strategy="epoch",
    save_strategy="epoch",
    learning_rate=2e-5,
    per_device_train_batch_size=8,
    per_device_eval_batch_size=8,
    num_train_epochs=3,
    weight_decay=0.01,
    logging_dir='./logs',
    logging_steps=10,
    logging_first_step=True,
    log_level='info'
)

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=preprocessed_train_rl1,
    eval_dataset=preprocessed_valid_rl1 ,
    compute_metrics=compute_qa_metrics(tokenizer, preprocessed_valid_rl1["input_ids"])
)

trainer.train()

PyTorch: setting up devices
The default value for the training argument `--report_to` will change in v5 (from all installed integrations to none). In v5, you will need to use `--report_to all` to get the same behavior as now. You should start updating your code and make this info disappear :-).
***** Running training *****
  Num examples = 82
  Num Epochs = 3
  Instantaneous batch size per device = 8
  Total train batch size (w. parallel, distributed & accumulation) = 8
  Gradient Accumulation steps = 1
  Total optimization steps = 33
  Number of trainable parameters = 81,529,346


***** Running Evaluation *****
  Num examples = 14
  Batch size = 8


F1: 0.2676
Exact match: 0.07142857142857142
Precision: 0.2169
Recall: 0.3492


Saving model checkpoint to ./results/fine-tuned/remove_long/qa_1/checkpoint-11
Configuration saved in ./results/fine-tuned/remove_long/qa_1/checkpoint-11/config.json
Model weights saved in ./results/fine-tuned/remove_long/qa_1/checkpoint-11/model.safetensors
***** Running Evaluation *****
  Num examples = 14
  Batch size = 8


F1: 0.0379
Exact match: 0.07142857142857142
Precision: 0.0325
Recall: 0.0455


Saving model checkpoint to ./results/fine-tuned/remove_long/qa_1/checkpoint-22
Configuration saved in ./results/fine-tuned/remove_long/qa_1/checkpoint-22/config.json
Model weights saved in ./results/fine-tuned/remove_long/qa_1/checkpoint-22/model.safetensors
***** Running Evaluation *****
  Num examples = 14
  Batch size = 8


F1: 0.0379
Exact match: 0.07142857142857142
Precision: 0.0337
Recall: 0.0434


Saving model checkpoint to ./results/fine-tuned/remove_long/qa_1/checkpoint-33
Configuration saved in ./results/fine-tuned/remove_long/qa_1/checkpoint-33/config.json
Model weights saved in ./results/fine-tuned/remove_long/qa_1/checkpoint-33/model.safetensors


Training completed. Do not forget to share your model on huggingface.co/models =)




TrainOutput(global_step=33, training_loss=2.096869642084295, metrics={'train_runtime': 63.9451, 'train_samples_per_second': 3.847, 'train_steps_per_second': 0.516, 'total_flos': 32140662607872.0, 'train_loss': 2.096869642084295, 'epoch': 3.0})

In [52]:
save_dir_rl2 = './results/fine-tuned/remove_long/qa_1/model'
trainer.save_model(save_dir_rl2)
tokenizer.save_pretrained(save_dir_rl2)


Saving model checkpoint to ./results/fine-tuned/remove_long/qa_1/model
Configuration saved in ./results/fine-tuned/remove_long/qa_1/model/config.json
Model weights saved in ./results/fine-tuned/remove_long/qa_1/model/model.safetensors
tokenizer config file saved in ./results/fine-tuned/remove_long/qa_1/model/tokenizer_config.json
Special tokens file saved in ./results/fine-tuned/remove_long/qa_1/model/special_tokens_map.json


('./results/fine-tuned/remove_long/qa_1/model/tokenizer_config.json',
 './results/fine-tuned/remove_long/qa_1/model/special_tokens_map.json',
 './results/fine-tuned/remove_long/qa_1/model/vocab.json',
 './results/fine-tuned/remove_long/qa_1/model/merges.txt',
 './results/fine-tuned/remove_long/qa_1/model/added_tokens.json',
 './results/fine-tuned/remove_long/qa_1/model/tokenizer.json')

In [53]:
# Load the fine-tuned model and tokenizer
model = trainer.model

training_args = TrainingArguments(
    output_dir='results/fine-tuned/remove_long/qa_1/eval',
    per_device_eval_batch_size=8,
)

trainer = Trainer(
    model=model,
    args=training_args,
    eval_dataset=preprocessed_test_rl1,
    compute_metrics=compute_qa_metrics(tokenizer, preprocessed_test_rl1["input_ids"]) # ako trebam predati input_ids, a oni su ovisni o datasetu, koje predajem?
)
trainer.evaluate()

PyTorch: setting up devices
The default value for the training argument `--report_to` will change in v5 (from all installed integrations to none). In v5, you will need to use `--report_to all` to get the same behavior as now. You should start updating your code and make this info disappear :-).
***** Running Evaluation *****
  Num examples = 24
  Batch size = 8


F1: 0.1275
Exact match: 0.20833333333333334
Precision: 0.1106
Recall: 0.1505


{'eval_loss': 2.7459487915039062,
 'eval_Precision': 0.11056511056511056,
 'eval_Recall': 0.1505016722408027,
 'eval_F1': 0.1274787535410765,
 'eval_Exact match': 0.20833333333333334,
 'eval_runtime': 0.1707,
 'eval_samples_per_second': 140.564,
 'eval_steps_per_second': 17.571}

Model3

In [32]:
preprocessed_test_rl2 = clean_test_stringified.map(preprocess_dataset_remove_long, batched=True, remove_columns=col_names, fn_kwargs={"tokenizer":qa_tokenizers[2]})
preprocessed_train_rl2 = clean_train_stringified.map(preprocess_dataset_remove_long, batched=True, remove_columns=col_names, fn_kwargs={"tokenizer":qa_tokenizers[2]})
preprocessed_valid_rl2 = clean_valid_stringified.map(preprocess_dataset_remove_long, batched=True, remove_columns=col_names, fn_kwargs={"tokenizer":qa_tokenizers[2]})

Map:   0%|          | 0/825 [00:00<?, ? examples/s]

In [54]:
training_args = TrainingArguments(
    output_dir="./results/pretrained/remove_long/qa_2",
    per_device_eval_batch_size=4,
)
model = qa_models[2]
tokenizer = qa_tokenizers[2]

dataset = preprocessed_test_rl2
res = run_eval(model, tokenizer, dataset, training_args)

PyTorch: setting up devices
The default value for the training argument `--report_to` will change in v5 (from all installed integrations to none). In v5, you will need to use `--report_to all` to get the same behavior as now. You should start updating your code and make this info disappear :-).


Map:   0%|          | 0/825 [00:00<?, ? examples/s]

Map:   0%|          | 0/2640 [00:00<?, ? examples/s]

Map:   0%|          | 0/656 [00:00<?, ? examples/s]

***** Running Evaluation *****
  Num examples = 433
  Batch size = 4


F1: 0.2298
Exact match: 0.24942263279445728
Precision: 0.2097
Recall: 0.2542
{'eval_loss': 4.061172962188721, 'eval_Precision': 0.20972435534718292, 'eval_Recall': 0.2541634012539185, 'eval_F1': 0.2298153151158156, 'eval_Exact match': 0.24942263279445728, 'eval_runtime': 58.9491, 'eval_samples_per_second': 7.345, 'eval_steps_per_second': 1.849}


In [35]:
model = qa_models[2]
tokenizer = qa_tokenizers[2]

training_args = TrainingArguments(
    output_dir='./results/fine-tuned/remove_long/qa_2',
    eval_strategy="epoch",
    save_strategy="epoch",
    learning_rate=2e-5,
    per_device_train_batch_size=1,
    per_device_eval_batch_size=1,
    num_train_epochs=3,
    weight_decay=0.01,
    logging_dir='./logs',
    logging_steps=10,
    logging_first_step=True,
    log_level='info'
)

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=preprocessed_train_rl2,
    eval_dataset=preprocessed_valid_rl2,
    compute_metrics=compute_qa_metrics(tokenizer, preprocessed_valid_rl2["input_ids"])
)

trainer.train()

PyTorch: setting up devices
The default value for the training argument `--report_to` will change in v5 (from all installed integrations to none). In v5, you will need to use `--report_to all` to get the same behavior as now. You should start updating your code and make this info disappear :-).
***** Running training *****
  Num examples = 1,359
  Num Epochs = 3
  Instantaneous batch size per device = 1
  Total train batch size (w. parallel, distributed & accumulation) = 1
  Gradient Accumulation steps = 1
  Total optimization steps = 4,077
  Number of trainable parameters = 278,220,290


***** Running Evaluation *****
  Num examples = 334
  Batch size = 1


F1: 0.1659
Exact match: 0.23652694610778444
Precision: 0.1451
Recall: 0.1935


Saving model checkpoint to ./results/fine-tuned/remove_long/qa_2/checkpoint-1359
Configuration saved in ./results/fine-tuned/remove_long/qa_2/checkpoint-1359/config.json
Model weights saved in ./results/fine-tuned/remove_long/qa_2/checkpoint-1359/model.safetensors
***** Running Evaluation *****
  Num examples = 334
  Batch size = 1


F1: 0.1558
Exact match: 0.24251497005988024
Precision: 0.1315
Recall: 0.1912


Saving model checkpoint to ./results/fine-tuned/remove_long/qa_2/checkpoint-2718
Configuration saved in ./results/fine-tuned/remove_long/qa_2/checkpoint-2718/config.json
Model weights saved in ./results/fine-tuned/remove_long/qa_2/checkpoint-2718/model.safetensors
***** Running Evaluation *****
  Num examples = 334
  Batch size = 1


F1: 0.1792
Exact match: 0.25449101796407186
Precision: 0.1527
Recall: 0.2170


Saving model checkpoint to ./results/fine-tuned/remove_long/qa_2/checkpoint-4077
Configuration saved in ./results/fine-tuned/remove_long/qa_2/checkpoint-4077/config.json
Model weights saved in ./results/fine-tuned/remove_long/qa_2/checkpoint-4077/model.safetensors


Training completed. Do not forget to share your model on huggingface.co/models =)




TrainOutput(global_step=4077, training_loss=1.9905685392597419, metrics={'train_runtime': 2105.7855, 'train_samples_per_second': 1.936, 'train_steps_per_second': 1.936, 'total_flos': 4261304459649024.0, 'train_loss': 1.9905685392597419, 'epoch': 3.0})

In [ ]:
save_dir_rl3 = './results/fine-tuned/remove_long/qa_2/model'
trainer.save_model(save_dir_rl3)
tokenizer.save_pretrained(save_dir_rl3)


In [37]:
# Load the fine-tuned model and tokenizer
model = trainer.model

training_args = TrainingArguments(
    output_dir='results/fine-tuned/remove_long/qa_2/eval',
    per_device_eval_batch_size=8,
)

trainer = Trainer(
    model=model,
    args=training_args,
    eval_dataset=preprocessed_test_rl2,
    compute_metrics=compute_qa_metrics(tokenizer, preprocessed_test_rl2["input_ids"]) # ako trebam predati input_ids, a oni su ovisni o datasetu, koje predajem?
)
trainer.evaluate()

PyTorch: setting up devices
The default value for the training argument `--report_to` will change in v5 (from all installed integrations to none). In v5, you will need to use `--report_to all` to get the same behavior as now. You should start updating your code and make this info disappear :-).
***** Running Evaluation *****
  Num examples = 433
  Batch size = 8


F1: 0.2080
Exact match: 0.24249422632794457
Precision: 0.1863
Recall: 0.2355


{'eval_loss': 4.425774097442627,
 'eval_Precision': 0.18630338733431517,
 'eval_Recall': 0.23545258620689655,
 'eval_F1': 0.20801419360422344,
 'eval_Exact match': 0.24249422632794457,
 'eval_runtime': 58.926,
 'eval_samples_per_second': 7.348,
 'eval_steps_per_second': 0.933}

## Prediction aggregation

### Helper functions

In [32]:
def preprocess_dataset_paragraph(dataset, tokenizer):
    max_length = tokenizer.model_max_length
    if max_length is None or max_length > 2048:
        max_length = 2048
    contexts = dataset["context"]
    answers = dataset["answers"]

    start_positions = []
    end_positions = []

    inputs = tokenizer(
          dataset["question"],
          dataset["context"],
          max_length=max_length,
          truncation="only_second",
          padding="max_length",
          return_offsets_mapping=True,
    )

    offset_mapping = inputs.pop("offset_mapping")

    for i, offsets in enumerate(offset_mapping):
          answer = answers[i]
          context = contexts[i]
          start_char = context.find(answer)
          end_char = start_char + len(answer)

          start_position = None
          end_position = None

          for j, (start, end) in enumerate(offsets):
              if start <= start_char < end:
                  start_position = j
              if start < end_char <= end:
                  end_position = j

          # Ensure we have valid positions
          if start_position is None or end_position is None:
              start_positions.append(0)
              end_positions.append(0)
          else:
              start_positions.append(start_position)
              end_positions.append(end_position)

    inputs.update({
        "id": dataset["id"],
        "start_positions": start_positions,
        "end_positions": end_positions
    })
    return inputs

In [33]:
def get_predictions(out):
    start_preds = []
    end_preds = []
    predictions = []
    confidences = []
    start_pred, end_pred = out
    for start, end in zip(start_pred, end_pred):
        # Get the most likely start and end of the answer span
        start_pred = torch.argmax(torch.tensor(start))
        end_pred = torch.argmax(torch.tensor(end))

        # Collect the answer and its confidence score
        confidence = start[start_pred] + end[end_pred]
        start_preds.append(start_pred)
        end_preds.append(end_pred)
        confidences.append(confidence)
    predictions = {"start_pred": start_preds, "end_pred": end_preds, "confidence": confidences}
    return predictions


def aggregate_predictions(predictions):
    final_confidence_index = np.argmax(predictions["confidence"])
    final_start_pred = predictions["start_pred"][final_confidence_index]
    final_end_pred = predictions["end_pred"][final_confidence_index]

    return final_start_pred, final_end_pred, final_confidence_index


def compute_metrics_paragraph(tokenizer, input_ids):
    def compute_metrics(p):
        tp=0
        em=0
        total_pred=0
        total_ref=0

        start_preds, end_preds = p.predictions
        start_labels, end_labels = p.label_ids
        # Convert to lists of dictionaries as expected by the squad metric
        for i, (start_pred, end_pred, start_true, end_true) in enumerate(zip(start_preds, end_preds, start_labels, end_labels)):

            start_pred = int(start_pred)
            end_pred = int(end_pred)
            predicted_span = tokenizer.decode(input_ids[i][start_pred:end_pred+1])

            true_span = tokenizer.decode(input_ids[i][start_true:end_true+1])

            em += start_pred == start_true and end_pred == end_true

            tp += sum([len(set(p.split())&set(r.split())) for p, r in zip(predicted_span, true_span)])
            total_pred += sum([len(p.split()) for p in predicted_span])
            total_ref += sum([len(r.split()) for r in true_span])
        precision = tp/total_pred
        recall = tp/total_ref
        f1 = 2 * (precision * recall) / (precision + recall)
        em = em/len(start_preds)

        print(f"F1: {f1:.4f}")
        print(f"Exact match: {em}")
        print(f"Precision: {precision:.4f}")
        print(f"Recall: {recall:.4f}")

        return {"Precision":precision, "Recall": recall,"F1": f1, "Exact match": em}
    return compute_metrics


In [34]:
def eval_paragraphs(dataset, trainer, tokenizer):
    unique_ids = set(dataset['id'])
    pred_starts = []
    pred_ends = []
    labels_start = []
    labels_end = []
    final_input_ids = []

    grouped_entries = defaultdict(list)
    for entry in dataset:
        if entry["id"] in unique_ids:
            # Filter entries with the same id
            grouped_entries[entry["id"]].append(entry)

    print("grouped all entries")
    for k,v in grouped_entries.items():
        # Filter entries with the same id
        # entries = dataset.filter(lambda x: x["id"] == unique_id)
        # [entry for entry in dataset if entry['id'] == unique_id

        # Get predictions for all contexts
        predict_logits, label_ids, metrics = trainer.predict(v)
        predictions = get_predictions(predict_logits)
        # Aggregate predictions to get the final answer
        pred_start, pred_end, index = aggregate_predictions(predictions)

        # output should be logits
        pred_starts.append(pred_start)
        pred_ends.append(pred_end)
        labels_start.append(label_ids[0][index])
        labels_end.append(label_ids[1][index])
        final_input_ids.append(v[index]["input_ids"])

    final_predictions = EvalPrediction(predictions=(pred_starts, pred_ends), label_ids= (torch.tensor(labels_start), torch.tensor(labels_end)))
    metric_fn = compute_metrics_paragraph(tokenizer, final_input_ids)
    res = metric_fn(final_predictions)
    return res

### Model 1

#### Unfiltered

In [41]:
preprocessed_train_aggregate0 = clean_train_paragraphs.map(preprocess_dataset_paragraph, batched=True, remove_columns=col_names, fn_kwargs={"tokenizer":qa_tokenizers[0]})
preprocessed_valid_aggregate0 = clean_valid_paragraphs.map(preprocess_dataset_paragraph, batched=True, remove_columns=col_names, fn_kwargs={"tokenizer":qa_tokenizers[0]})
preprocessed_test_aggregate0 = clean_test_paragraphs.map(preprocess_dataset_paragraph, batched=True, remove_columns=col_names, fn_kwargs={"tokenizer":qa_tokenizers[0]})

Map:   0%|          | 0/32580 [00:00<?, ? examples/s]

Map:   0%|          | 0/8232 [00:00<?, ? examples/s]

Map:   0%|          | 0/10557 [00:00<?, ? examples/s]

In [46]:
dataset = preprocessed_test_aggregate0
model = qa_models[0]
tokenizer = qa_tokenizers[0]

training_args = TrainingArguments(
    output_dir="./results/pretrained/aggregate/qa_0",
    per_device_eval_batch_size=8,
)

trainer = Trainer(
        model=model,
        args=training_args,
        tokenizer=tokenizer,
    )

results = eval_paragraphs(dataset, trainer, tokenizer)
print(results)

PyTorch: setting up devices
The default value for the training argument `--report_to` will change in v5 (from all installed integrations to none). In v5, you will need to use `--report_to all` to get the same behavior as now. You should start updating your code and make this info disappear :-).
***** Running Prediction *****
  Num examples = 17
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.


grouped all entries


***** Running Prediction *****
  Num examples = 10
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.


***** Running Prediction *****
  Num examples = 21
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.


***** Running Prediction *****
  Num examples = 18
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.


...

***** Running Prediction *****
  Num examples = 11
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.


***** Running Prediction *****
  Num examples = 7
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.


***** Running Prediction *****
  Num examples = 8
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.


***** Running Prediction *****
  Num examples = 29
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.


F1: 0.2344
Exact match: 0.6193939447402954
Precision: 0.2405
Recall: 0.2286
{'Precision': 0.24054611531283765, 'Recall': 0.22855809612692488, 'F1': 0.2343989280245023, 'Exact match': tensor(0.6194)}


##### Fine-tuning

In [42]:
model = qa_models[0]
tokenizer = qa_tokenizers[0]
training_args = TrainingArguments(
    output_dir='./results/fine-tuned/aggregate/qa_0',
    eval_strategy="epoch",
    save_strategy="epoch",
    learning_rate=2e-5,
    per_device_train_batch_size=8,
    per_device_eval_batch_size=8,
    num_train_epochs=3,
    weight_decay=0.01,
    logging_dir='./logs',
    logging_steps=10,
    logging_first_step=True,
    log_level='info'
)

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset= preprocessed_train_aggregate0,
    eval_dataset=preprocessed_valid_aggregate0,
    tokenizer=tokenizer,
    compute_metrics=compute_qa_metrics(tokenizer, preprocessed_valid_aggregate0["input_ids"]),
)
trainer.train()

PyTorch: setting up devices
The default value for the training argument `--report_to` will change in v5 (from all installed integrations to none). In v5, you will need to use `--report_to all` to get the same behavior as now. You should start updating your code and make this info disappear :-).
The following columns in the training set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.
***** Running training *****
  Num examples = 32,580
  Num Epochs = 3
  Instantaneous batch size per device = 8
  Total train batch size (w. parallel, distributed & accumulation) = 8
  Gradient Accumulation steps = 1
  Total optimization steps = 12,219
  Number of trainable parameters = 124,056,578


The following columns in the evaluation set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.
***** Running Evaluation *****
  Num examples = 8232
  Batch size = 8


F1: 0.5065
Exact match: 0.8841107871720116
Precision: 0.7423
Recall: 0.3844


Saving model checkpoint to ./results/fine-tuned/aggregate/qa_0/checkpoint-4073
Configuration saved in ./results/fine-tuned/aggregate/qa_0/checkpoint-4073/config.json
Model weights saved in ./results/fine-tuned/aggregate/qa_0/checkpoint-4073/model.safetensors
tokenizer config file saved in ./results/fine-tuned/aggregate/qa_0/checkpoint-4073/tokenizer_config.json
Special tokens file saved in ./results/fine-tuned/aggregate/qa_0/checkpoint-4073/special_tokens_map.json
The following columns in the evaluation set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.
***** Running Evaluation *****
  Num examples = 8232
  Batch size = 8


F1: 0.4843
Exact match: 0.8788872691933917
Precision: 0.5934
Recall: 0.4091


Saving model checkpoint to ./results/fine-tuned/aggregate/qa_0/checkpoint-8146
Configuration saved in ./results/fine-tuned/aggregate/qa_0/checkpoint-8146/config.json
Model weights saved in ./results/fine-tuned/aggregate/qa_0/checkpoint-8146/model.safetensors
tokenizer config file saved in ./results/fine-tuned/aggregate/qa_0/checkpoint-8146/tokenizer_config.json
Special tokens file saved in ./results/fine-tuned/aggregate/qa_0/checkpoint-8146/special_tokens_map.json
The following columns in the evaluation set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.
***** Running Evaluation *****
  Num examples = 8232
  Batch size = 8


F1: 0.4871
Exact match: 0.8737852283770651
Precision: 0.5541
Recall: 0.4346


Saving model checkpoint to ./results/fine-tuned/aggregate/qa_0/checkpoint-12219
Configuration saved in ./results/fine-tuned/aggregate/qa_0/checkpoint-12219/config.json
Model weights saved in ./results/fine-tuned/aggregate/qa_0/checkpoint-12219/model.safetensors
tokenizer config file saved in ./results/fine-tuned/aggregate/qa_0/checkpoint-12219/tokenizer_config.json
Special tokens file saved in ./results/fine-tuned/aggregate/qa_0/checkpoint-12219/special_tokens_map.json


Training completed. Do not forget to share your model on huggingface.co/models =)




TrainOutput(global_step=12219, training_loss=0.39444780870903184, metrics={'train_runtime': 3523.4915, 'train_samples_per_second': 27.74, 'train_steps_per_second': 3.468, 'total_flos': 2.553914500337664e+16, 'train_loss': 0.39444780870903184, 'epoch': 3.0})

In [43]:
dataset = preprocessed_test_aggregate0
model = trainer.model

training_args = TrainingArguments(
    output_dir="./results/pretrained/aggregate/qa_0",
    per_device_eval_batch_size=8,
)

trainer = Trainer(
        model=model,
        args=training_args,
        tokenizer=tokenizer,
    )

results = eval_paragraphs(dataset, trainer, tokenizer)
print(results)

PyTorch: setting up devices
The default value for the training argument `--report_to` will change in v5 (from all installed integrations to none). In v5, you will need to use `--report_to all` to get the same behavior as now. You should start updating your code and make this info disappear :-).
***** Running Prediction *****
  Num examples = 17
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.


grouped all entries


***** Running Prediction *****
  Num examples = 10
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.


***** Running Prediction *****
  Num examples = 21
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.


***** Running Prediction *****
  Num examples = 18
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.


...

***** Running Prediction *****
  Num examples = 11
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.


***** Running Prediction *****
  Num examples = 7
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.


***** Running Prediction *****
  Num examples = 8
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.


***** Running Prediction *****
  Num examples = 29
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.


F1: 0.5572
Exact match: 0.8133333325386047
Precision: 0.6082
Recall: 0.5141
{'Precision': 0.6082435945042703, 'Recall': 0.5141242937853108, 'F1': 0.5572376254465046, 'Exact match': tensor(0.8133)}


#### Filtered

In [47]:
filtered_testset0 = preprocessed_test_aggregate0.filter(lambda x: x["start_positions"]!= 0 and x["end_positions"]!= 0)
filtered_trainset0 = preprocessed_train_aggregate0.filter(lambda x: x["start_positions"]!= 0 and x["end_positions"]!= 0)
filtered_validset0 = preprocessed_valid_aggregate0.filter(lambda x: x["start_positions"]!= 0 and x["end_positions"]!= 0)

Filter:   0%|          | 0/10557 [00:00<?, ? examples/s]

Filter:   0%|          | 0/32580 [00:00<?, ? examples/s]

Filter:   0%|          | 0/8232 [00:00<?, ? examples/s]

In [48]:
dataset = filtered_testset0
model = qa_models[0]
tokenizer = qa_tokenizers[0]

training_args = TrainingArguments(
    output_dir="./results/fine-tuned/aggregate/qa_0",
    per_device_eval_batch_size=8,
)

trainer = Trainer(
        model=model,
        args=training_args,
        tokenizer=tokenizer,
    )

results = eval_paragraphs(dataset, trainer, tokenizer)
print(results)

PyTorch: setting up devices
The default value for the training argument `--report_to` will change in v5 (from all installed integrations to none). In v5, you will need to use `--report_to all` to get the same behavior as now. You should start updating your code and make this info disappear :-).
***** Running Prediction *****
  Num examples = 11
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.


grouped all entries


***** Running Prediction *****
  Num examples = 1
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.


***** Running Prediction *****
  Num examples = 1
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.


***** Running Prediction *****
  Num examples = 1
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.


...

***** Running Prediction *****
  Num examples = 1
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.


***** Running Prediction *****
  Num examples = 1
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.


***** Running Prediction *****
  Num examples = 1
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.


***** Running Prediction *****
  Num examples = 1
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.


F1: 0.0793
Exact match: 0.1008717343211174
Precision: 0.1684
Recall: 0.0519
{'Precision': 0.16837927857699667, 'Recall': 0.05189132523805364, 'F1': 0.07933354480041402, 'Exact match': tensor(0.1009)}


In [49]:
model = qa_models[0]
tokenizer = qa_tokenizers[0]

training_args = TrainingArguments(
    output_dir='./results/fine-tuned/aggregate/qa_0',
    eval_strategy="epoch",
    save_strategy="epoch",
    learning_rate=2e-5,
    per_device_train_batch_size=8,
    per_device_eval_batch_size=8,
    num_train_epochs=3,
    weight_decay=0.01,
    logging_dir='./logs',
    logging_steps=10,
    logging_first_step=True,
    log_level='info'
)

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset= filtered_trainset0,
    eval_dataset=filtered_validset0,
    tokenizer=tokenizer,
    compute_metrics=compute_qa_metrics(tokenizer, filtered_validset0["input_ids"]),
)
trainer.train()

PyTorch: setting up devices
The default value for the training argument `--report_to` will change in v5 (from all installed integrations to none). In v5, you will need to use `--report_to all` to get the same behavior as now. You should start updating your code and make this info disappear :-).
The following columns in the training set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.
***** Running training *****
  Num examples = 3,737
  Num Epochs = 3
  Instantaneous batch size per device = 8
  Total train batch size (w. parallel, distributed & accumulation) = 8
  Gradient Accumulation steps = 1
  Total optimization steps = 1,404
  Number of trainable parameters = 124,056,578


The following columns in the evaluation set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.
***** Running Evaluation *****
  Num examples = 1015
  Batch size = 8


F1: 0.3258
Exact match: 0.4147783251231527
Precision: 0.3193
Recall: 0.3325


Saving model checkpoint to ./results/fine-tuned/aggregate/qa_0/checkpoint-468
Configuration saved in ./results/fine-tuned/aggregate/qa_0/checkpoint-468/config.json
Model weights saved in ./results/fine-tuned/aggregate/qa_0/checkpoint-468/model.safetensors
tokenizer config file saved in ./results/fine-tuned/aggregate/qa_0/checkpoint-468/tokenizer_config.json
Special tokens file saved in ./results/fine-tuned/aggregate/qa_0/checkpoint-468/special_tokens_map.json
The following columns in the evaluation set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.
***** Running Evaluation *****
  Num examples = 1015
  Batch size = 8


F1: 0.3166
Exact match: 0.41379310344827586
Precision: 0.3132
Recall: 0.3202


Saving model checkpoint to ./results/fine-tuned/aggregate/qa_0/checkpoint-936
Configuration saved in ./results/fine-tuned/aggregate/qa_0/checkpoint-936/config.json
Model weights saved in ./results/fine-tuned/aggregate/qa_0/checkpoint-936/model.safetensors
tokenizer config file saved in ./results/fine-tuned/aggregate/qa_0/checkpoint-936/tokenizer_config.json
Special tokens file saved in ./results/fine-tuned/aggregate/qa_0/checkpoint-936/special_tokens_map.json
The following columns in the evaluation set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.
***** Running Evaluation *****
  Num examples = 1015
  Batch size = 8


F1: 0.3225
Exact match: 0.3980295566502463
Precision: 0.2971
Recall: 0.3526


Saving model checkpoint to ./results/fine-tuned/aggregate/qa_0/checkpoint-1404
Configuration saved in ./results/fine-tuned/aggregate/qa_0/checkpoint-1404/config.json
Model weights saved in ./results/fine-tuned/aggregate/qa_0/checkpoint-1404/model.safetensors
tokenizer config file saved in ./results/fine-tuned/aggregate/qa_0/checkpoint-1404/tokenizer_config.json
Special tokens file saved in ./results/fine-tuned/aggregate/qa_0/checkpoint-1404/special_tokens_map.json


Training completed. Do not forget to share your model on huggingface.co/models =)




TrainOutput(global_step=1404, training_loss=1.1065635589452891, metrics={'train_runtime': 451.5625, 'train_samples_per_second': 24.827, 'train_steps_per_second': 3.109, 'total_flos': 2929397939767296.0, 'train_loss': 1.1065635589452891, 'epoch': 3.0})

In [50]:
dataset = filtered_testset0
model = trainer.model
training_args = TrainingArguments(
    output_dir="./results/pretrained/aggregate/qa_0",
    per_device_eval_batch_size=8,
)

trainer = Trainer(
        model=model,
        args=training_args,
        tokenizer=tokenizer,
    )

results = eval_paragraphs(dataset, trainer, tokenizer)
print(results)

PyTorch: setting up devices
The default value for the training argument `--report_to` will change in v5 (from all installed integrations to none). In v5, you will need to use `--report_to all` to get the same behavior as now. You should start updating your code and make this info disappear :-).
***** Running Prediction *****
  Num examples = 11
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.


grouped all entries


***** Running Prediction *****
  Num examples = 1
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.


***** Running Prediction *****
  Num examples = 1
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.


***** Running Prediction *****
  Num examples = 1
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.


...

***** Running Prediction *****
  Num examples = 1
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.


***** Running Prediction *****
  Num examples = 1
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.


***** Running Prediction *****
  Num examples = 1
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.


***** Running Prediction *****
  Num examples = 1
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.


F1: 0.3455
Exact match: 0.3374844193458557
Precision: 0.3608
Recall: 0.3314
{'Precision': 0.3607789058227728, 'Recall': 0.33141134844712355, 'F1': 0.34547213842563607, 'Exact match': tensor(0.3375)}


### Model 2

#### Unfiltered

In [35]:
preprocessed_train_aggregate1 = clean_train_paragraphs.map(preprocess_dataset_paragraph, batched=True, remove_columns=col_names, fn_kwargs={"tokenizer":qa_tokenizers[1]})
preprocessed_valid_aggregate1 = clean_valid_paragraphs.map(preprocess_dataset_paragraph, batched=True, remove_columns=col_names, fn_kwargs={"tokenizer":qa_tokenizers[1]})
preprocessed_test_aggregate1 = clean_test_paragraphs.map(preprocess_dataset_paragraph, batched=True, remove_columns=col_names, fn_kwargs={"tokenizer":qa_tokenizers[1]})

Map:   0%|          | 0/32580 [00:00<?, ? examples/s]

Map:   0%|          | 0/8232 [00:00<?, ? examples/s]

Map:   0%|          | 0/10557 [00:00<?, ? examples/s]

In [45]:
dataset = preprocessed_test_aggregate1
model = qa_models[1]
tokenizer = qa_tokenizers[1]

training_args = TrainingArguments(
    output_dir="./results/fine-tuned/aggregate/qa_1",
    per_device_eval_batch_size=8,
)

trainer = Trainer(
        model=model,
        args=training_args,
        tokenizer=tokenizer,
    )

results = eval_paragraphs(dataset, trainer, tokenizer)
print(results)

PyTorch: setting up devices
The default value for the training argument `--report_to` will change in v5 (from all installed integrations to none). In v5, you will need to use `--report_to all` to get the same behavior as now. You should start updating your code and make this info disappear :-).
***** Running Prediction *****
  Num examples = 17
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.


grouped all entries


***** Running Prediction *****
  Num examples = 10
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.


***** Running Prediction *****
  Num examples = 21
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.


***** Running Prediction *****
  Num examples = 18
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.


...

***** Running Prediction *****
  Num examples = 11
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.


***** Running Prediction *****
  Num examples = 7
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.


***** Running Prediction *****
  Num examples = 8
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.


***** Running Prediction *****
  Num examples = 29
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.


F1: 0.1569
Exact match: 0.1539393961429596
Precision: 0.1150
Recall: 0.2468
{'Precision': 0.11504795117698344, 'Recall': 0.24680182539088802, 'F1': 0.15693829979544266, 'Exact match': tensor(0.1539)}


In [46]:
model = qa_models[1]
tokenizer = qa_tokenizers[1]
training_args = TrainingArguments(
    output_dir='./results/fine-tuned/aggregate/qa_1',
    eval_strategy="epoch",
    save_strategy="epoch",
    learning_rate=2e-5,
    per_device_train_batch_size=8,
    per_device_eval_batch_size=8,
    num_train_epochs=3,
    weight_decay=0.01,
    logging_dir='./logs',
    logging_steps=10,
    logging_first_step=True,
    log_level='info'
)

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset= preprocessed_train_aggregate1,
    eval_dataset=preprocessed_valid_aggregate1,
    tokenizer=tokenizer,
    compute_metrics=compute_qa_metrics(tokenizer, preprocessed_valid_aggregate1["input_ids"]),
)
trainer.train()

PyTorch: setting up devices
The default value for the training argument `--report_to` will change in v5 (from all installed integrations to none). In v5, you will need to use `--report_to all` to get the same behavior as now. You should start updating your code and make this info disappear :-).
The following columns in the training set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.
***** Running training *****
  Num examples = 32,580
  Num Epochs = 3
  Instantaneous batch size per device = 8
  Total train batch size (w. parallel, distributed & accumulation) = 8
  Gradient Accumulation steps = 1
  Total optimization steps = 12,219
  Number of trainable parameters = 81,529,346


The following columns in the evaluation set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.
***** Running Evaluation *****
  Num examples = 8232
  Batch size = 8


F1: 0.5072
Exact match: 0.8780369290573372
Precision: 0.8095
Recall: 0.3693


Saving model checkpoint to ./results/fine-tuned/aggregate/qa_1/checkpoint-4073
Configuration saved in ./results/fine-tuned/aggregate/qa_1/checkpoint-4073/config.json
Model weights saved in ./results/fine-tuned/aggregate/qa_1/checkpoint-4073/model.safetensors
tokenizer config file saved in ./results/fine-tuned/aggregate/qa_1/checkpoint-4073/tokenizer_config.json
Special tokens file saved in ./results/fine-tuned/aggregate/qa_1/checkpoint-4073/special_tokens_map.json
The following columns in the evaluation set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.
***** Running Evaluation *****
  Num examples = 8232
  Batch size = 8


F1: 0.4806
Exact match: 0.8689261418853256
Precision: 0.6264
Recall: 0.3899


Saving model checkpoint to ./results/fine-tuned/aggregate/qa_1/checkpoint-8146
Configuration saved in ./results/fine-tuned/aggregate/qa_1/checkpoint-8146/config.json
Model weights saved in ./results/fine-tuned/aggregate/qa_1/checkpoint-8146/model.safetensors
tokenizer config file saved in ./results/fine-tuned/aggregate/qa_1/checkpoint-8146/tokenizer_config.json
Special tokens file saved in ./results/fine-tuned/aggregate/qa_1/checkpoint-8146/special_tokens_map.json
The following columns in the evaluation set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.
***** Running Evaluation *****
  Num examples = 8232
  Batch size = 8


F1: 0.4739
Exact match: 0.8650388726919339
Precision: 0.5571
Recall: 0.4124


Saving model checkpoint to ./results/fine-tuned/aggregate/qa_1/checkpoint-12219
Configuration saved in ./results/fine-tuned/aggregate/qa_1/checkpoint-12219/config.json
Model weights saved in ./results/fine-tuned/aggregate/qa_1/checkpoint-12219/model.safetensors
tokenizer config file saved in ./results/fine-tuned/aggregate/qa_1/checkpoint-12219/tokenizer_config.json
Special tokens file saved in ./results/fine-tuned/aggregate/qa_1/checkpoint-12219/special_tokens_map.json


Training completed. Do not forget to share your model on huggingface.co/models =)




TrainOutput(global_step=12219, training_loss=0.37347688060185263, metrics={'train_runtime': 1882.3988, 'train_samples_per_second': 51.923, 'train_steps_per_second': 6.491, 'total_flos': 1.277003399712768e+16, 'train_loss': 0.37347688060185263, 'epoch': 3.0})

In [47]:
dataset = preprocessed_test_aggregate1
model = trainer.model
training_args = TrainingArguments(
    output_dir="./results/fine-tuned/aggregate/qa_1",
    per_device_eval_batch_size=8,
)

trainer = Trainer(
        model=model,
        args=training_args,
        tokenizer=tokenizer,
    )

results = eval_paragraphs(dataset, trainer, tokenizer)
print(results)

PyTorch: setting up devices
The default value for the training argument `--report_to` will change in v5 (from all installed integrations to none). In v5, you will need to use `--report_to all` to get the same behavior as now. You should start updating your code and make this info disappear :-).
***** Running Prediction *****
  Num examples = 17
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.


grouped all entries


***** Running Prediction *****
  Num examples = 10
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.


***** Running Prediction *****
  Num examples = 21
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.


***** Running Prediction *****
  Num examples = 18
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.


...

***** Running Prediction *****
  Num examples = 11
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.


***** Running Prediction *****
  Num examples = 7
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.


***** Running Prediction *****
  Num examples = 8
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.


***** Running Prediction *****
  Num examples = 29
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.


F1: 0.4456
Exact match: 0.8012121319770813
Precision: 0.7065
Recall: 0.3254
{'Precision': 0.7064549180327869, 'Recall': 0.32542772861356933, 'F1': 0.44559334356571617, 'Exact match': tensor(0.8012)}


#### Filtered

In [36]:
filtered_testset1 = preprocessed_test_aggregate1.filter(lambda x: x["start_positions"]!= 0 and x["end_positions"]!= 0)
filtered_trainset1 = preprocessed_train_aggregate1.filter(lambda x: x["start_positions"]!= 0 and x["end_positions"]!= 0)
filtered_validset1 = preprocessed_valid_aggregate1.filter(lambda x: x["start_positions"]!= 0 and x["end_positions"]!= 0)

Filter:   0%|          | 0/10557 [00:00<?, ? examples/s]

Filter:   0%|          | 0/32580 [00:00<?, ? examples/s]

Filter:   0%|          | 0/8232 [00:00<?, ? examples/s]

In [37]:
dataset = filtered_testset1
model = qa_models[1]
tokenizer = qa_tokenizers[1]

training_args = TrainingArguments(
    output_dir="./results/fine-tuned/aggregate/qa_1",
    per_device_eval_batch_size=8,
)

trainer = Trainer(
        model=model,
        args=training_args,
        tokenizer=tokenizer,
    )

results = eval_paragraphs(dataset, trainer, tokenizer)
print(results)

grouped all entries


F1: 0.0542
Exact match: 0.05230386182665825
Precision: 0.1712
Recall: 0.0322
{'Precision': 0.1711994421199442, 'Recall': 0.03216859576326709, 'F1': 0.05416038533661802, 'Exact match': tensor(0.0523)}


In [38]:
model = qa_models[1]
tokenizer = qa_tokenizers[1]

training_args = TrainingArguments(
    output_dir='./results/fine-tuned/aggregate/qa_1',
    eval_strategy="epoch",
    save_strategy="epoch",
    learning_rate=2e-5,
    per_device_train_batch_size=8,
    per_device_eval_batch_size=8,
    num_train_epochs=3,
    weight_decay=0.01,
    logging_dir='./logs',
    logging_steps=10,
    logging_first_step=True,
    log_level='info'
)

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset= filtered_trainset1,
    eval_dataset=filtered_validset1,
    tokenizer=tokenizer,
    compute_metrics=compute_qa_metrics(tokenizer, filtered_validset1["input_ids"]),
)
trainer.train()

The following columns in the training set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.
***** Running training *****
  Num examples = 3,737
  Num Epochs = 3
  Instantaneous batch size per device = 8
  Total train batch size (w. parallel, distributed & accumulation) = 8
  Gradient Accumulation steps = 1
  Total optimization steps = 1,404
  Number of trainable parameters = 81,529,346


The following columns in the evaluation set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.
***** Running Evaluation *****
  Num examples = 1015
  Batch size = 8


F1: 0.2986
Exact match: 0.36354679802955664
Precision: 0.2589
Recall: 0.3526


Saving model checkpoint to ./results/fine-tuned/aggregate/qa_1/checkpoint-468
Configuration saved in ./results/fine-tuned/aggregate/qa_1/checkpoint-468/config.json
Model weights saved in ./results/fine-tuned/aggregate/qa_1/checkpoint-468/model.safetensors
tokenizer config file saved in ./results/fine-tuned/aggregate/qa_1/checkpoint-468/tokenizer_config.json
Special tokens file saved in ./results/fine-tuned/aggregate/qa_1/checkpoint-468/special_tokens_map.json
The following columns in the evaluation set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.
***** Running Evaluation *****
  Num examples = 1015
  Batch size = 8


F1: 0.2761
Exact match: 0.34088669950738915
Precision: 0.2414
Recall: 0.3225


Saving model checkpoint to ./results/fine-tuned/aggregate/qa_1/checkpoint-936
Configuration saved in ./results/fine-tuned/aggregate/qa_1/checkpoint-936/config.json
Model weights saved in ./results/fine-tuned/aggregate/qa_1/checkpoint-936/model.safetensors
tokenizer config file saved in ./results/fine-tuned/aggregate/qa_1/checkpoint-936/tokenizer_config.json
Special tokens file saved in ./results/fine-tuned/aggregate/qa_1/checkpoint-936/special_tokens_map.json
The following columns in the evaluation set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.
***** Running Evaluation *****
  Num examples = 1015
  Batch size = 8


F1: 0.2799
Exact match: 0.3438423645320197
Precision: 0.2479
Recall: 0.3213


Saving model checkpoint to ./results/fine-tuned/aggregate/qa_1/checkpoint-1404
Configuration saved in ./results/fine-tuned/aggregate/qa_1/checkpoint-1404/config.json
Model weights saved in ./results/fine-tuned/aggregate/qa_1/checkpoint-1404/model.safetensors
tokenizer config file saved in ./results/fine-tuned/aggregate/qa_1/checkpoint-1404/tokenizer_config.json
Special tokens file saved in ./results/fine-tuned/aggregate/qa_1/checkpoint-1404/special_tokens_map.json


Training completed. Do not forget to share your model on huggingface.co/models =)




TrainOutput(global_step=1404, training_loss=1.2735645652156948, metrics={'train_runtime': 253.2338, 'train_samples_per_second': 44.271, 'train_steps_per_second': 5.544, 'total_flos': 1464751904458752.0, 'train_loss': 1.2735645652156948, 'epoch': 3.0})

In [39]:
dataset = filtered_testset1
model = trainer.model

training_args = TrainingArguments(
    output_dir="./results/fine-tuned/aggregate/qa_1",
    per_device_eval_batch_size=8,
)

trainer = Trainer(
        model=model,
        args=training_args,
        tokenizer=tokenizer,
    )

results = eval_paragraphs(dataset, trainer, tokenizer)
print(results)

PyTorch: setting up devices
The default value for the training argument `--report_to` will change in v5 (from all installed integrations to none). In v5, you will need to use `--report_to all` to get the same behavior as now. You should start updating your code and make this info disappear :-).
***** Running Prediction *****
  Num examples = 11
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.


grouped all entries


***** Running Prediction *****
  Num examples = 1
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.


***** Running Prediction *****
  Num examples = 1
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.


***** Running Prediction *****
  Num examples = 1
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.


...

***** Running Prediction *****
  Num examples = 1
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.


***** Running Prediction *****
  Num examples = 1
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.


***** Running Prediction *****
  Num examples = 1
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.


***** Running Prediction *****
  Num examples = 1
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.


F1: 0.3174
Exact match: 0.280199259519577
Precision: 0.3282
Recall: 0.3073
{'Precision': 0.3281639887129498, 'Recall': 0.3073361434468299, 'F1': 0.3174087607705147, 'Exact match': tensor(0.2802)}


### Model 3

#### Unfiltered

In [35]:
preprocessed_train_aggregate2 = clean_train_paragraphs.map(preprocess_dataset_paragraph, batched=True, remove_columns=col_names, fn_kwargs={"tokenizer":qa_tokenizers[2]})
preprocessed_valid_aggregate2 = clean_valid_paragraphs.map(preprocess_dataset_paragraph, batched=True, remove_columns=col_names, fn_kwargs={"tokenizer":qa_tokenizers[2]})
preprocessed_test_aggregate2 = clean_test_paragraphs.map(preprocess_dataset_paragraph, batched=True, remove_columns=col_names, fn_kwargs={"tokenizer":qa_tokenizers[2]})

Map:   0%|          | 0/32580 [00:00<?, ? examples/s]

Map:   0%|          | 0/8232 [00:00<?, ? examples/s]

Map:   0%|          | 0/10557 [00:00<?, ? examples/s]

In [50]:
dataset = preprocessed_test_aggregate2
model = qa_models[2]
tokenizer = qa_tokenizers[2]

training_args = TrainingArguments(
    output_dir="./results/fine-tuned/aggregate/qa_2",
    per_device_eval_batch_size=4,
)

trainer = Trainer(
        model=model,
        args=training_args,
        tokenizer=tokenizer,
    )

results = eval_paragraphs(dataset, trainer, tokenizer)
print(results)

PyTorch: setting up devices
The default value for the training argument `--report_to` will change in v5 (from all installed integrations to none). In v5, you will need to use `--report_to all` to get the same behavior as now. You should start updating your code and make this info disappear :-).
***** Running Prediction *****
  Num examples = 17
  Batch size = 4
The following columns in the test set don't have a corresponding argument in `DebertaV2ForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `DebertaV2ForQuestionAnswering.forward`,  you can safely ignore this message.


grouped all entries


***** Running Prediction *****
  Num examples = 10
  Batch size = 4
The following columns in the test set don't have a corresponding argument in `DebertaV2ForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `DebertaV2ForQuestionAnswering.forward`,  you can safely ignore this message.


***** Running Prediction *****
  Num examples = 21
  Batch size = 4
The following columns in the test set don't have a corresponding argument in `DebertaV2ForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `DebertaV2ForQuestionAnswering.forward`,  you can safely ignore this message.


***** Running Prediction *****
  Num examples = 18
  Batch size = 4
The following columns in the test set don't have a corresponding argument in `DebertaV2ForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `DebertaV2ForQuestionAnswering.forward`,  you can safely ignore this message.


...

***** Running Prediction *****
  Num examples = 11
  Batch size = 4
The following columns in the test set don't have a corresponding argument in `DebertaV2ForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `DebertaV2ForQuestionAnswering.forward`,  you can safely ignore this message.


***** Running Prediction *****
  Num examples = 7
  Batch size = 4
The following columns in the test set don't have a corresponding argument in `DebertaV2ForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `DebertaV2ForQuestionAnswering.forward`,  you can safely ignore this message.


***** Running Prediction *****
  Num examples = 8
  Batch size = 4
The following columns in the test set don't have a corresponding argument in `DebertaV2ForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `DebertaV2ForQuestionAnswering.forward`,  you can safely ignore this message.


***** Running Prediction *****
  Num examples = 29
  Batch size = 4
The following columns in the test set don't have a corresponding argument in `DebertaV2ForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `DebertaV2ForQuestionAnswering.forward`,  you can safely ignore this message.


F1: 0.2711
Exact match: 0.5806060433387756
Precision: 0.2674
Recall: 0.2749
{'Precision': 0.26742783629492645, 'Recall': 0.27492147462390476, 'F1': 0.2711228856735276, 'Exact match': tensor(0.5806)}


In [36]:
model = qa_models[2]
tokenizer = qa_tokenizers[2]
training_args = TrainingArguments(
    output_dir='./results/fine-tuned/aggregate/qa_2',
    eval_strategy="epoch",
    save_strategy="epoch",
    learning_rate=2e-5,
    per_device_train_batch_size=8,
    per_device_eval_batch_size=8,
    num_train_epochs=3,
    weight_decay=0.01,
    logging_dir='./logs',
    logging_steps=10,
    logging_first_step=True,
    log_level='info'
)

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset= preprocessed_train_aggregate2,
    eval_dataset=preprocessed_valid_aggregate2,
    tokenizer=tokenizer,
    compute_metrics=compute_qa_metrics(tokenizer, preprocessed_valid_aggregate2["input_ids"]),
)
trainer.train()

The following columns in the training set don't have a corresponding argument in `DebertaV2ForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `DebertaV2ForQuestionAnswering.forward`,  you can safely ignore this message.
***** Running training *****
  Num examples = 32,580
  Num Epochs = 3
  Instantaneous batch size per device = 8
  Total train batch size (w. parallel, distributed & accumulation) = 8
  Gradient Accumulation steps = 1
  Total optimization steps = 12,219
  Number of trainable parameters = 278,220,290


OutOfMemoryError: CUDA out of memory. Tried to allocate 1.50 GiB. GPU 

In [ ]:
dataset = preprocessed_test_aggregate2
model = trainer.model
training_args = TrainingArguments(
    output_dir="./results/fine-tuned/aggregate/qa_2",
    per_device_eval_batch_size=8,
)

trainer = Trainer(
        model=model,
        args=training_args,
        tokenizer=tokenizer,
    )

results = eval_paragraphs(dataset, trainer, tokenizer)
print(results)

#### Filtered

In [36]:
filtered_testset2 = preprocessed_test_aggregate2.filter(lambda x: x["start_positions"]!= 0 and x["end_positions"]!= 0)
filtered_trainset2 = preprocessed_train_aggregate2.filter(lambda x: x["start_positions"]!= 0 and x["end_positions"]!= 0)
filtered_validset2 = preprocessed_valid_aggregate2.filter(lambda x: x["start_positions"]!= 0 and x["end_positions"]!= 0)

Filter:   0%|          | 0/10557 [00:00<?, ? examples/s]

Filter:   0%|          | 0/32580 [00:00<?, ? examples/s]

Filter:   0%|          | 0/8232 [00:00<?, ? examples/s]

In [52]:
dataset = filtered_testset2
model = qa_models[2]
tokenizer = qa_tokenizers[2]

training_args = TrainingArguments(
    output_dir="./results/fine-tuned/aggregate/qa_2",
    per_device_eval_batch_size=8,
)

trainer = Trainer(
        model=model,
        args=training_args,
        tokenizer=tokenizer,
    )

results = eval_paragraphs(dataset, trainer, tokenizer)
print(results)

PyTorch: setting up devices
The default value for the training argument `--report_to` will change in v5 (from all installed integrations to none). In v5, you will need to use `--report_to all` to get the same behavior as now. You should start updating your code and make this info disappear :-).
***** Running Prediction *****
  Num examples = 11
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `DebertaV2ForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `DebertaV2ForQuestionAnswering.forward`,  you can safely ignore this message.


grouped all entries


***** Running Prediction *****
  Num examples = 1
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `DebertaV2ForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `DebertaV2ForQuestionAnswering.forward`,  you can safely ignore this message.


***** Running Prediction *****
  Num examples = 1
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `DebertaV2ForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `DebertaV2ForQuestionAnswering.forward`,  you can safely ignore this message.


***** Running Prediction *****
  Num examples = 1
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `DebertaV2ForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `DebertaV2ForQuestionAnswering.forward`,  you can safely ignore this message.


...

***** Running Prediction *****
  Num examples = 1
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `DebertaV2ForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `DebertaV2ForQuestionAnswering.forward`,  you can safely ignore this message.


***** Running Prediction *****
  Num examples = 1
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `DebertaV2ForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `DebertaV2ForQuestionAnswering.forward`,  you can safely ignore this message.


***** Running Prediction *****
  Num examples = 1
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `DebertaV2ForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `DebertaV2ForQuestionAnswering.forward`,  you can safely ignore this message.


***** Running Prediction *****
  Num examples = 1
  Batch size = 8
The following columns in the test set don't have a corresponding argument in `DebertaV2ForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `DebertaV2ForQuestionAnswering.forward`,  you can safely ignore this message.


F1: 0.1174
Exact match: 0.12453299760818481
Precision: 0.1855
Recall: 0.0858
{'Precision': 0.18554023422742727, 'Recall': 0.08582162906009043, 'F1': 0.11735890198186896, 'Exact match': tensor(0.1245)}


In [38]:
model = qa_models[2]
tokenizer = qa_tokenizers[2]

training_args = TrainingArguments(
    output_dir='./results/fine-tuned/aggregate/qa_2',
    eval_strategy="epoch",
    save_strategy="epoch",
    learning_rate=2e-5,
    per_device_train_batch_size=4,
    per_device_eval_batch_size=4,
    num_train_epochs=3,
    weight_decay=0.01,
    logging_dir='./logs',
    logging_steps=10,
    logging_first_step=True,
    log_level='info'
)

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset= filtered_trainset2,
    eval_dataset=filtered_validset2,
    tokenizer=tokenizer,
    compute_metrics=compute_qa_metrics(tokenizer, filtered_validset2["input_ids"]),
)
trainer.train()

PyTorch: setting up devices
The default value for the training argument `--report_to` will change in v5 (from all installed integrations to none). In v5, you will need to use `--report_to all` to get the same behavior as now. You should start updating your code and make this info disappear :-).
The following columns in the training set don't have a corresponding argument in `DebertaV2ForQuestionAnswering.forward` and have been ignored: id. If id are not expected by `DebertaV2ForQuestionAnswering.forward`,  you can safely ignore this message.
***** Running training *****
  Num examples = 3,735
  Num Epochs = 3
  Instantaneous batch size per device = 4
  Total train batch size (w. parallel, distributed & accumulation) = 4
  Gradient Accumulation steps = 1
  Total optimization steps = 2,802
  Number of trainable parameters = 278,220,290


OutOfMemoryError: CUDA out of memory. Tried to allocate 768.00 MiB. GPU 

In [ ]:
dataset = filtered_testset2
model = trainer.model

training_args = TrainingArguments(
    output_dir="./results/fine-tuned/aggregate/qa_2",
    per_device_eval_batch_size=8,
)

trainer = Trainer(
        model=model,
        args=training_args,
        tokenizer=tokenizer,
    )

results = eval_paragraphs(dataset, trainer, tokenizer)
print(results)